# Data Cleaning & Quality Checks


In this notebook I perform the data cleaning and basic data quality checks for all the datasets used in this project. The goal is to transform the raw GeoJSON files into clean GeoDataFrames that can be used for exploratory data analysis and spatial analysis.

This includes:
- Basic preprocessing (column selection, data types, CRS)
- Consistency and validity checks
- Spatial validity checks
- Fixing or removing invalid records

The cleaned datasets are saved into the `data/processed/` folder and will be used in the EDA notebooks.

## 1. Source
The following datasets were downloaded from the Buenos Aires open data portal.

For more info about each dataset and their columns, visit the following links:


- **Dataset:** Paradas de Colectivo (GeoJSON)

    - **Link:** [Buenos Aires Data - Paradas de Colectivo][bus_stops]

- **Dataset:** Callejero (GeoJSON)

    - **Link:** [Buenos Aires Data - Callejero][callejero]

- **Dataset:** Comunas (GeoJSON)

    - **Link:** [Buenos Aires Data - Comunas][comunas]

- **Dataset** Barrios (GeoJSON)
    - **Link:** [Buenos Aires Data - Barios][barrios]

[bus_stops]: https://data.buenosaires.gob.ar/dataset/colectivos-paradas/resource/e9699a48-7189-499f-ab3b-d164fd7a1730
[callejero]: https://data.buenosaires.gob.ar/dataset/calles/resource/juqdkmgo-301-resource
[comunas]: https://data.buenosaires.gob.ar/dataset/comunas/resource/b0b627ac-5b47-4574-89ac-6999b63598ee
[barrios]: https://data.buenosaires.gob.ar/dataset/barrios/resource/1c3d185b-fdc9-474b-b41b-9bd960a3806e

## 2. Imports

In [1]:
import pandas as pd
import geopandas as gpd
import numpy as np
from normalize_columns import normalize_columns
from normalize_strings import normalize_strings
from shapely.geometry import box
from pathlib import Path
import sys

ModuleNotFoundError: No module named 'normalize_columns'

## 3. Loading Data

In [ ]:
sys.path.append(str(Path.cwd().parent / "src"))
PROJECT_ROOT = Path.cwd().parent 
DATA_PATH = PROJECT_ROOT / "data" / "raw" 

DATA_PATH.exists()

True

In [ ]:
stops_raw = gpd.read_file(DATA_PATH / "paradas-de-colectivo.geojson")

# Make a copy in order to leave the original file intact
stops = stops_raw.copy()
stops[["DIRECCION", "COMUNA", "BARRIO", "L1", "l1_sen", "L2", "geometry"]].head(3)

DIRECCION COMUNA       BARRIO   L1 l1_sen    L2  \
0          1524 DEFENSA      1    SAN TELMO   22      V    53   
1          1528 DEFENSA      1    SAN TELMO   29      I  None   
2  906 MITRE, BARTOLOME      1  SAN NICOLAS  105      V  None   

                      geometry  
0  POINT (-58.37099 -34.62566)  
1    POINT (-58.371 -34.62571)  
2  POINT (-58.37966 -34.60722)

In [ ]:
calles_raw = gpd.read_file(DATA_PATH / "callejero.geojson")
calles = calles_raw.copy()
calles[["nomoficial", "alt_izqini", "alt_izqfin", "comuna", "barrio", "geometry"]].head(3)

nomoficial  alt_izqini  alt_izqfin  comuna barrio  \
0          CANTILO, INT.           0           0    13.0  Nuñez   
1  LUGONES, LEOPOLDO AV.           0           0    13.0  Nuñez   
2         PAZ, GRAL. AV.           2         300    13.0  Nuñez   

                                            geometry  
0  LINESTRING (-58.46219 -34.53452, -58.46267 -34...  
1  LINESTRING (-58.46515 -34.53465, -58.46496 -34...  
2  LINESTRING (-58.46561 -34.53507, -58.46577 -34...

In [ ]:
comunas_raw = gpd.read_file(DATA_PATH / "comunas.geojson")
comunas = comunas_raw.copy()
comunas.head(3)

id  objeto  comuna                                            barrios  \
0   1  COMUNA       1  Constitucion, San Telmo, Monserrat, Retiro, Pu...   
1   2  COMUNA       2                                           Recoleta   
2   3  COMUNA       3                           San Cristobal, Balvanera   

   perimetro         area                                           geometry  
0   36351.19  17801036.28  MULTIPOLYGON (((-58.34892 -34.61698, -58.34901...  
1   25965.02   6433391.77  POLYGON ((-58.38039 -34.56847, -58.38037 -34.5...  
2   10486.26   6385992.08  POLYGON ((-58.41192 -34.59801, -58.4103 -34.59...

In [ ]:
barrios_raw = gpd.read_file(DATA_PATH / "barrios.geojson")
barrios = barrios_raw.copy()
barrios.head(3)

id  objeto     nombre  comuna  perimetro_  area_metro  \
0   1  BARRIO  Agronomia      15     6556.17  2122169.54   
1   2  BARRIO    Almagro       5     8537.90  4050752.63   
2   3  BARRIO  Balvanera       3     8375.82  4342280.68   

                                            geometry  
0  POLYGON ((-58.47589 -34.59173, -58.47598 -34.5...  
1  POLYGON ((-58.416 -34.59786, -58.4157 -34.5978...  
2  POLYGON ((-58.39294 -34.59964, -58.39277 -34.6...

## 4. calles dataset cleaning

### 4.1 Columns
Let's have a look at the available columns. Only the columns required for name matching and spatial analysis are kept. Column names are then normalized to lowercase and snake_case for consistency.


In [ ]:
calles.columns

Index(['id', 'codigo', 'nomoficial', 'alt_izqini', 'alt_izqfin', 'alt_derini',
       'alt_derfin', 'nomanter', 'nom_mapa', 'tipo_c', 'long', 'sentido',
       'observa', 'bicisenda', 'red_jerarq', 'tipo_ffcc', 'comuna', 'com_par',
       'com_impar', 'barrio', 'barrio_par', 'barrio_imp', 'geometry'],
      dtype='object')

Attributes related to traffic direction, or infrastructure are dropped, as they are not relevant for the current analysis. I will rename the **nom_oficial** column to **calle** for simplification.


In [ ]:
cols_to_keep = [
    "nomoficial", "barrio", "barrio_par", "barrio_imp",
    "comuna", "com_par", "com_impar", "geometry"
]

calles = calles[cols_to_keep].rename(columns={"nomoficial": "calle"})
calles.columns = normalize_columns(calles.columns)
calles.columns

Index(['calle', 'barrio', 'barrio_par', 'barrio_imp', 'comuna', 'com_par',
       'com_impar', 'geometry'],
      dtype='object')

### 4.2 Dtypes

In [ ]:
calles.dtypes

calle           object
barrio          object
barrio_par      object
barrio_imp      object
comuna         float64
com_par        float64
com_impar      float64
geometry      geometry
dtype: object

Let's convert the columns **comuna**, **com_par** and **com_impar** to integers (communes are integers):

In [ ]:
cols_to_convert = ["comuna","com_par","com_impar"]
for col in cols_to_convert:
    calles[col] = pd.to_numeric(calles[col], errors="coerce").astype('Int64')

calles[cols_to_convert].dtypes

comuna       Int64
com_par      Int64
com_impar    Int64
dtype: object

### 4.3 String normalization

In [ ]:
cols_to_norm = ["calle", "barrio", "barrio_par", "barrio_imp"]

for col in cols_to_norm:
    calles[col] = calles[col].apply(
        lambda x: normalize_strings(x)
    )

### 4.4 Data Quality

Percentage of missing values:

In [ ]:
calles.isna().mean() * 100

calle         0.000000
barrio        5.409887
barrio_par    0.275344
barrio_imp    0.278473
comuna        5.409887
com_par       0.275344
com_impar     0.278473
geometry      0.000000
dtype: float64

Most columns show almost no missing values. The only exceptions are barrio and comuna, with about 5.4% missing values. This is expected, since many street segments are shared between two neighborhoods or communes. In those cases, the information is stored separately for even and odd sides of the street. There are no missing geometries, so the dataset is safe to use for spatial analysis.

In [ ]:
calles

calle         barrio     barrio_par  \
0                      CANTILO INT          NUÑEZ          NUÑEZ   
1              LUGONES LEOPOLDO AV          NUÑEZ          NUÑEZ   
2                      PAZ GRAL AV          NUÑEZ          NUÑEZ   
3                DEL LIBERTADOR AV          NUÑEZ          NUÑEZ   
4            COLECTORA CANTILO INT          NUÑEZ          NUÑEZ   
...                            ...            ...            ...   
31955  OBLIGADO RAFAEL AVCOSTANERA        PALERMO        PALERMO   
31956  OBLIGADO RAFAEL AVCOSTANERA        PALERMO        PALERMO   
31957  OBLIGADO RAFAEL AVCOSTANERA        PALERMO        PALERMO   
31958  OBLIGADO RAFAEL AVCOSTANERA        PALERMO        PALERMO   
31959    ACHAVAL RODRIGUEZ T DR AV  PUERTO MADERO  PUERTO MADERO   

          barrio_imp  comuna  com_par  com_impar  \
0              NUÑEZ      13       13         13   
1              NUÑEZ      13       13         13   
2              NUÑEZ      13       13         13   
3              NUÑEZ      13       13         13   
4              NUÑEZ      13       13         13   
...              ...     ...      ...        ...   
31955        PALERMO      14       14         14   
31956        PALERMO      14       14         14   
31957        PALERMO      14       14         14   
31958        PALERMO      14       14         14   
31959  PUERTO MADERO       1        1          1   

                                                geometry  
0      LINESTRING (-58.46219 -34.53452, -58.46267 -34...  
1      LINESTRING (-58.46515 -34.53465, -58.46496 -34...  
2      LINESTRING (-58.46561 -34.53507, -58.46577 -34...  
3      LINESTRING (-58.46676 -34.53593, -58.46681 -34...  
4      LINESTRING (-58.46065 -34.53512, -58.4608 -34....  
...                                                  ...  
31955  LINESTRING (-58.41329 -34.55608, -58.4141 -34....  
31956  LINESTRING (-58.41644 -34.55471, -58.41713 -34...  
31957  LINESTRING (-58.41082 -34.55752, -58.4109 -34....  
31958  LINESTRING (-58.4132 -34.55597, -58.41329 -34....  
31959  LINESTRING (-58.35644 -34.61775, -58.35643 -34...  

[31960 rows x 8 columns]

### 4.5 Aggregating street segments

Streets are stored as many small segments, which is great for mapping but not very convenient for analysis. Here I group all segments by street name, merging their geometries and keeping track of all the neighborhoods and communes they pass through. This gives me a cleaner, street-level view of the data

In [ ]:
from shapely.ops import unary_union

def unique_values(series):
    return sorted(set(series.dropna()))

calles_agg = (
    calles
    .groupby("calle")
    .agg({
        "barrio_par": unique_values,
        "barrio_imp": unique_values,
        "com_par": unique_values,
        "com_impar": unique_values,
        "geometry": lambda l: unary_union(l)
    })
    .reset_index()
)

calles_agg["barrios"] = (calles_agg["barrio_par"] + calles_agg["barrio_imp"]).apply(lambda x: sorted(set(x)))

calles_agg["comunas"] = (calles_agg["com_par"] + calles_agg["com_impar"]).apply(lambda x: sorted(set(x)))

calles_agg = calles_agg.drop(columns=["barrio_par", "barrio_imp", "com_par", "com_impar"])

In [ ]:
calles_agg = gpd.GeoDataFrame(
    calles_agg,
    geometry="geometry",
    crs=calles.crs
)

In [ ]:
calles_agg.explore()

In [ ]:
calles